# **P2 - Transcriptómica II 2025**

This Google Colab notebook (R) demonstrates integration and differential gene testing between conditions. We are starting with the two seurat objects from a mouse experiment. One sample was collected from the spleen of a naive mouse, and the second sample from the spleen of a parasite-infected mouse.

**1. Install packages**

In [ ]:
install.packages("Seurat", quietly=TRUE)

In [ ]:
## Bioconductor

if (!require("BiocManager", quietly = TRUE))
    install.packages("BiocManager")

BiocManager::install("glmGamPoi", quietly=TRUE, ask=FALSE, update=FALSE)

In [ ]:
system("pip3 install leidenalg")

In [ ]:
library(tidyverse) #preinstalled in Google Colab
library(Seurat)
library(patchwork)

In [ ]:
#added to make the axis labels and titles and legend titles larger in Google Colab
theme(axis.text = element_text(size = 12),
      axis.title = element_text(size = 14),
      legend.title = element_text(size = 14))

**2. Load Seurat objects**

To demonstrate integration we need at least two samples or at least two modalities for the same sample (e.g. RNA-seq and ATAC-seq). In this case, we will use two samples, one generated from the spleen of a untreated mouse (control), and the second from the spleen of mouse infected with a parasite. Each sample was processed with the typical Seurat workflow. Then, the Seurat objects were saved into RData files. Upload and read the provided objects to the Colab space.

In [ ]:
#Read in the two Seurat objects
#control / NAIVE
load("P3/spleen.naive.seu")
spleen.naive.seu
DimPlot(spleen.naive.seu, reduction = "umap", split.by = "orig.ident", label = TRUE)


In [ ]:
#INFECTED
load("P3/spleen.infected.seu")
spleen.infected.seu
DimPlot(spleen.infected.seu, reduction = "umap", split.by = "orig.ident", label = TRUE)

How many assays are there in each sample? How many cells? How many clusters? Do the samples show the same number of clusters? Which sample shows more classes of cells?

Since we are now going to work with multiple samples, we need a study design file with our sample metadata.

In [ ]:
#read study design
targets <- read_tsv("P3/studyDesign_P3.txt", show_col_types = FALSE)
targets

In [ ]:
# extract variables of interest
sampleID <- targets$sampleID
treatment <- targets$treatment

# annotate your seurat objects with as much or as little metadata as you want!
spleen.naive.seu$treatment <- treatment[1]
spleen.infected.seu$treatment <- treatment[2]

# take a look at where this metadata lives in the seurat object
head(spleen.infected.seu@meta.data)


**3. INTEGRATION**

Integration of single-cell sequencing datasets, for example across experimental batches, donors, or conditions, is often an important step in scRNA-seq workflows. Integrative analysis can help to match shared cell types and states across datasets, which can boost statistical power, and most importantly, facilitate accurate comparative analysis across datasets.

In this case, we will integrate the two conditions together, so that we can jointly identify cell subpopulations across datasets, and then explore how each group differs across conditions. In other words, we now aim to integrate data from the two treatments, so that cells from the same cell type will cluster together.

We often refer to this procedure as intergration/alignment. When aligning two genome sequences together, identification of shared/homologous regions can help to interpret differences between the sequences as well. Similarly for scRNA-seq integration, our goal is not to remove biological differences across conditions, but to learn shared cell types/states in an initial step - specifically because that will enable us to compare infected and control profiles for these individual cell types.



Seurat identifies shared sources of variation between the conditions/groups. It is a form of PCA, in that it identifies the greatest sources of variation in the data, but only if it is shared or conserved across the conditions/groups (using the 2000 most variant genes from each sample).

This step roughly aligns the cells using the greatest shared sources of variation.

NOTE: The shared highly variable genes are used because they are the most likely to represent those genes distinguishing the different cell types present.

Identify anchors or mutual nearest neighbors (MNNs) across datasets (sometimes incorrect anchors are identified):

MNNs can be thought of as 'best buddies'. For each cell in one condition:

The cell's closest neighbor in the other condition is identified based on gene expression values - its 'best buddy'.
The reciprocal analysis is performed, and if the two cells are 'best buddies' in both directions, then those cells will be marked as anchors to 'anchor' the two datasets together.


In [ ]:
# select features that are repeatedly variable across datasets for integration
spleen_features <- SelectIntegrationFeatures(object.list = c(spleen.naive.seu, spleen.infected.seu))
spleen_anchors <- FindIntegrationAnchors(object.list = c(spleen.naive.seu, spleen.infected.seu), anchor.features = spleen_features)
spleen_integrated <- IntegrateData(anchorset = spleen_anchors)
# NOTE: if you look at your seurat object, the default assay as changed from 'RNA' to 'integrated'
# this can be change anytime using the line below
# this would be the same way you would change between scRNA-seq and scATAC-seq
# DefaultAssay(spleen_integrated) <- "RNA"


In [ ]:
?FindIntegrationAnchors

Please, pay attention to all the steps that Seurat took during this integration.

Now, for the integrated object, we have to repeat the standard workflow for visualization and clustering.

In [ ]:
spleen_integrated

In [ ]:
# Run the standard workflow for visualization and clustering
spleen_integrated <- ScaleData(spleen_integrated, verbose = FALSE)
spleen_integrated <- RunPCA(spleen_integrated, npcs = 50, verbose = FALSE)
PCAPlot(spleen_integrated)
ElbowPlot(spleen_integrated, 50)


What is colored in the previous PCA? Can you color the cells by sample?
How many principal components would you choose for the upcoming analysis steps?

In [ ]:
#Check the meta.data associated to spleen_integrated
head(spleen_integrated@meta.data,2)
tail(spleen_integrated@meta.data,2)


In [ ]:
PCAPlot(spleen_integrated, group.by="treatment")

Does the PCA suggest a cell type difference between naive and infected samples?

**4. Clusterization and visualization**


In [ ]:
#Clusterization and visualization
spleen_integrated <- RunUMAP(spleen_integrated, reduction = "pca", dims = 1:35)
spleen_integrated <- FindNeighbors(spleen_integrated, reduction = "pca", dims = 1:35)
spleen_integrated <- suppressWarnings(FindClusters(spleen_integrated, algorithm=4, resolution = 0.5))


In [ ]:
head(spleen_integrated@meta.data,2)

In [ ]:
DimPlot(spleen_integrated, reduction = "umap", label = TRUE)

Remember, we have metadata in this integrated seurat object, so you can use this to split your UMAP.

In [ ]:
options(repr.plot.width=16, repr.plot.height=9)

DimPlot(spleen_integrated, reduction="umap", label=TRUE,
split.by = "treatment", # this facets the plot
group.by = "seurat_clusters") #labels the cells with values from the group.by variable

We can have a look at the proportion of our total cells per cluster. We can do the same for each treatment.

In [ ]:
head(Idents(spleen_integrated))

In [ ]:
# let's see what proportion of our total cells reside in each cluster
#Total cells
prop.table(table(Idents(spleen_integrated)))

In [ ]:
#Naive
prop.table(table(Idents(subset(spleen_integrated, treatment=="naive"))))

In [ ]:
#Infected
prop.table(table(Idents(subset(spleen_integrated, treatment=="infected"))))

We can plot one or more genes of interest on the UMAP.

In [ ]:
FeaturePlot(spleen_integrated,
            reduction = "umap",
            features = 'Sdc1',
            pt.size = 0.4,
            order = TRUE,
            split.by = "treatment",
            min.cutoff = 'q10',
            label = FALSE)


In [ ]:
# we can plot more than one gene here
my.genes <- c("Cd4", "Cd8a")
FeaturePlot(spleen_integrated,
            reduction = "umap",
            features = my.genes,
            pt.size = 0.4,
            order = TRUE,
            split.by = "treatment",
            min.cutoff = 'q10',
            label = FALSE)

**To install before taking the break!!!!!!!!!!!!!!!!!!!**

In [ ]:
BiocManager::install("SingleR", quietly=TRUE, ask=FALSE, update=FALSE)
BiocManager::install("celldex", quietly=TRUE, ask=FALSE, update=FALSE)
install.packages("viridis", quietly=TRUE)
install.packages("pheatmap", quietly=TRUE)

In [ ]:
library(SingleR)
library(celldex)
library(viridis)
library(pheatmap)

**5. Cell type annnotation**

We will use SingleR for cell type annotation, in combination with the celldex package that stores cell type-specific expression data for mouse.


*It can also be useful to turn the Seurat object into a* **singleCellExperiment** *object, for better interoperability with other bioconductor tools.*



In [ ]:
MouseRNAseq.data <- MouseRNAseqData(ensembl = FALSE) #358 bulk RNA-seq samples of sorted cell populations

In [ ]:
MouseRNAseq.data
head(assays(MouseRNAseq.data)$logcounts)

In [ ]:
# Seurat allows you to convert directly to SingleCellExperiment object
# now let's run our cluster identification using SingleR
spleen_integrated.sce <- as.SingleCellExperiment(spleen_integrated)
predictions <- SingleR(test=spleen_integrated.sce, assay.type.test=1,
                       ref=MouseRNAseq.data, labels=MouseRNAseq.data$label.main)



In [ ]:
predictions

In [ ]:
table(predictions$labels)

In [ ]:
plotScoreHeatmap(predictions)

In [ ]:
spleen_integrated

In [ ]:
#now add back to singleCellExperiment object (or Seurat objects)
#spleen_integrated.sce[["SingleR.labels"]] <- predictions$labels
#plotUMAP(spleen_integrated.sce, colour_by = "SingleR.labels")
all(rownames(spleen_integrated@meta.data[1:5,]) == rownames(predictions[1:5,]))
all(rownames(spleen_integrated@meta.data[5995:6000,]) == rownames(predictions[5995:6000,]))

spleen_integrated@meta.data$SingleR.labels <- predictions$labels



In [ ]:
options(repr.plot.width=16, repr.plot.height=6)
UMAPPlot(spleen_integrated, group.by = c("seurat_clusters","SingleR.labels"), label = TRUE, label.size = 6) + NoLegend()

In [ ]:
UMAPPlot(spleen_integrated, split.by="treatment", group.by="SingleR.labels", label = TRUE, label.size = 6) + NoLegend()

In [ ]:
head(spleen_integrated@active.ident)
?Idents


In [ ]:
table(spleen_integrated@meta.data[,c("seurat_clusters","SingleR.labels")])

**6. Focus on a specific cluster for differential expression**

We can subset the Seurat object to focus on a specific cluster. Let's take the T cells as a working example. Then, we will analyze if there are any differentially expressed genes between the T cells of naive and infected mice.

In [ ]:
# subset seurat object to focus on single cluster ----
# let's get just the T cells
spleen_integrated.Tcells <- subset(spleen_integrated, subset = SingleR.labels == "T cells")
spleen_integrated.Tcells


In [ ]:
head(spleen_integrated.Tcells@meta.data,2)

In [ ]:
# now we need to switch out 'Idents' to be treatment, rather than cluster
Idents(spleen_integrated.Tcells) <- spleen_integrated.Tcells$treatment

In [ ]:
#Analyze differentially expressed genes (simple approach)
infected.vs.naive.de <- FindMarkers(object = spleen_integrated.Tcells,
                                    ident.1 = "infected",
                                    ident.2 = "naive",
                                    min.pct = 0)

infected.vs.naive.de$pct.diff <- infected.vs.naive.de$pct.1 - infected.vs.naive.de$pct.2
infected.vs.naive.de.df <- as_tibble(infected.vs.naive.de, rownames = "geneID")
head(infected.vs.naive.de.df)


In [ ]:
# Export DEGs for the cluster (ranked by avg_logFC > 0.5)
myTopHits <- subset(infected.vs.naive.de.df, p_val_adj<1e-30) %>% arrange(desc(avg_log2FC))
head(myTopHits,15)

In [ ]:
FeaturePlot(spleen_integrated,
            reduction = "umap",
            features = c("Depdc1a","Stil"),
            pt.size = 0.4,
            order = TRUE,
            split.by = "treatment",
            min.cutoff = 'q10',
            label = FALSE)


Here, we visualize the expression of these genes in a UMAP containing only T cells. This is a quick and convenient approach — but what do you think about its limitations?

In [ ]:
FeaturePlot(spleen_integrated.Tcells,
            reduction = "umap",
            features = c("Depdc1a","Stil"),
            pt.size = 0.4,
            order = TRUE,
            split.by = "treatment",
            min.cutoff = 'q10',
            label = FALSE)

**TASK**

Please, repeat the analysis for the monocyte/macrophage cells. Analyze and describe your results.

**QUESTION**

In case you have a dataset with a better design, for example a dataset with 3 control samples and 3 infected samples, would you use another method for the calculation of differentially expressed genes between infected and control spleen samples? Explain.